In [1]:
default_values = {"batch_size": 32, "epochs": 15, "learning_rate": 1e-2}

We want to study a good structure for Conv Networks. We will so follow common rules of thumb like:
- The number of filter may be mixed in increasing order to better match more complex patterns in the images
- A (3x3) kernel generally performs well
- CNN benefit from having a multiple succession of layers

For starters the epochs will be set to 20 and later studied as hyperparameter or regularized by Early Stopping.


We will also be using BatchNormalization as proposed by the paper:


# 1 - Load data
Total splitting of data will be [70%, 10%, 20%] (If we consider test and train to be the full set) <br />

In [2]:
import torch

from dataset.k_fold_dataset_wrapper import KFoldDatasetWrapper
from torch.utils.data import DataLoader
from dataset.dataset_loader import dataset_loader, dataset_information

train, test = dataset_loader((224, 224))
# Optionally fix the generator for reproducible results, e.g.: torch.Generator().manual_seed(42)
train, validation = torch.utils.data.random_split(train, [0.875, 0.125])

train_dataloader = DataLoader(dataset=train, batch_size=default_values["batch_size"], shuffle=True)
validation_dataloader = DataLoader(dataset=validation, batch_size=default_values["batch_size"], shuffle=True)
test_dataloader = DataLoader(dataset=test, batch_size=default_values["batch_size"], shuffle=True)

In [8]:
mean, variance = dataset_information(train, (224, 224))
measures = {"mean": mean, "variance": variance}

In [4]:
measures

# 2 - First model
Our first model is a simple CNN. <br><br />


## 2.1 - Model definition 

In [5]:
project_definition: dict[str, any] = {"name": "hand_tailored_v1"}

Here we report the first handbuilt model which can also found in ```models.conv_network.hand_tailored_conv_net.py```

In [4]:
from models.structure.augmentation_wrapper import NormalizedModelWrapper
from keras.layers import Conv2D, MaxPool2D, Input, Flatten, Dense, Layer


class HandTailoredConvNet(NormalizedModelWrapper):
    def make_layers(self, input_shape: (int, int, int)) -> tuple[Layer, Layer]:
        chan = self.data_format.value
        input_layer = Input(shape=input_shape, name=self.__class__.__name__)

        x = Conv2D(64, kernel_size=(3, 3), padding='same', data_format=chan, activation="relu")(input_layer)
        x = MaxPool2D(pool_size=(2, 2), data_format=chan)(x)

        x = Conv2D(filters=128, kernel_size=(3, 3), padding='same', data_format=chan, activation="relu")(x)
        x = MaxPool2D(pool_size=(2, 2), data_format=chan)(x)

        x = Flatten(data_format=chan)(x)
        x = Dense(units=128, activation="relu")(x)

        output_layer = Dense(units=1, activation="sigmoid")(x)
        return input_layer, output_layer

## 2.2 - Model instance and learning

In [7]:
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters

model_generator = HandTailoredConvNet()
model_generator.load_dataset_mean_and_variance(mean, variance)

model = model_generator.make_model((3, 224, 224))
SgdLearningParameters(learning_rate=default_values["learning_rate"]).compile_model(model)

model.summary()

The model is large

In [8]:
import keras

# We fix the number of epochs for now. Later we will add early stopping.
model.fit(x=train_dataloader, validation_data=validation_dataloader, epochs=default_values["epochs"], callbacks=[
    # To persist the history
    keras.callbacks.CSVLogger(f"{project_definition['name']}_train.csv", separator=",", append=True)
])

persist_model: bool = True
if persist_model:
    model.save(f'{project_definition["name"]}.keras')

In [9]:
res = model.evaluate(test_dataloader)
print(f"Test accuracy is {res[1] * 100:.2f}% while loss is {res[0]}")

## 2.4 - Results summary
> Test accuracy is 88.18% while loss is 0.6591373085975647

The model is clearly overfitting

In [9]:
from utils.data_processing import make_loss_graphs, make_loss_accuracy_graphs, add_tuner_iteration_to_data
import pandas

csv = pandas.read_csv(f"{project_definition['name']}_train.csv")
add_tuner_iteration_to_data(csv)

loss_graph = make_loss_graphs(csv)
acc_graph = make_loss_accuracy_graphs(csv)

loss_graph.update_layout(title="Loss vs Val_loss in tuner search per epoch (Val dashed)").show()
acc_graph.update_layout(title="Accuracy vs Val_Accuracy in tuner search per epoch (Val dashed)").show()

# 3 - Dataset Augmentation
To do data augmentation and overcome some keras bugs (if those really are bugs) we have to invert
the input shape on the data loaded by the ```torch.Dataloader```. Therefore we use the 
```AbstractAugmentationModel``` reported here. The reported class is stripped down to see augmentation in action, the real extended class in our experiments is ```TorchAugmentationModel```

In [1]:
from abc import ABC  # So that inverted augmentation wrapper stays an abstract class
from models.structure.augmentation_wrapper import AugmentationWrapperBase
import keras


class AbstractAugmentationModel(AugmentationWrapperBase, ABC):
    def make_augmentation(self, input_shape: (int, int, int)) -> tuple[keras.Layer, keras.Layer]:
        input_layer = keras.Input(shape=input_shape, name=self.__class__.__name__)
        x = keras.layers.Permute(dims=(2, 3, 1))(input_layer)  # Channels Last

        x = keras.layers.RandomFlip(mode="horizontal_and_vertical")(x)
        x = keras.layers.RandomRotation(0.3)(x)
        x = keras.layers.RandomBrightness(0.4, value_range=(0., 1.))(x)

        # Reset the shape so that the channels are first. 
        # We don't do it for this test as we need permuted images to see the augmentation in action
        # x = keras.layers.Permute(dims=(3, 2, 1))(x)
        return input_layer, x

## 3.1 - See augmentation in action
On some samples

In [91]:
import torch
import plotly.express as px
import numpy as np

aug_in, aug_out = AbstractAugmentationModel().make_augmentation((3, 224, 224))
aug_procedure = keras.Model(inputs=aug_in, outputs=aug_out)

VISUALIZE_SAMPLES: int = 8

image_list: list = []
for i in torch.rand(VISUALIZE_SAMPLES):
    image = train[int(i * len(test))][0]
    #image = torch.permute(image, (1, 2, 0))
    local_image = np.expand_dims(image, 0)

    # We add the original followed by the altered one
    image_list.append(torch.permute(image, (1, 2, 0)))
    image_list.append(np.squeeze(aug_procedure(local_image), 0))

image_list = [i.cpu() for i in image_list]
fig = px.imshow(np.array(image_list), facet_col=0, facet_col_wrap=4)

fig.update_layout(coloraxis_showscale=False, width=720, height=720, margin=dict(l=10, r=10, b=10, t=10))
fig.update_xaxes(showticklabels=False).update_yaxes(showticklabels=False)
fig.update_layout(width=720, height=720, margin=dict(l=10, r=10, b=10, t=10))

fig.show()

In [35]:
# Visualize 8 different versions of the image
VISUALIZE_SAMPLES: int = 7

image_list: list = []
image = train[int(torch.rand(1)[0] * len(test))][0]
image_list.append(torch.permute(image, (1, 2, 0)))
for i in range(VISUALIZE_SAMPLES):
    image_list.append(np.squeeze(aug_procedure(np.expand_dims(image, 0)), 0))

image_list = [i.cpu() for i in image_list]
fig = px.imshow(np.array(image_list), facet_col=0, facet_col_wrap=4)

fig.update_layout(coloraxis_showscale=False, width=700, height=400, margin=dict(l=5, r=5, b=5, t=5))
fig.update_xaxes(showticklabels=False).update_yaxes(showticklabels=False)
fig.update_layout(width=710, height=400, margin=dict(l=1, r=1, b=1, t=1))

fig.show()

\divThe augmentation procedure is so now handled by Keras and is actually part of the model.

> From now on on all models we apply directly the image augmentation procedure.

# 4 - First model with image augmentation


## 4.1 - Model definition

In [8]:
project_definition: dict[str, any] = {"name": "hand_tailored_v1_augmented"}

In [9]:
from models.structure.augmentation_wrapper import TorchAugmentationModel


class AugmentedHandTailoredConvNet(TorchAugmentationModel):
    def make_layers(self, input_shape: (int, int, int)) -> tuple[Layer, Layer]:
        chan = self.data_format.value
        input_layer = Input(shape=input_shape, name=self.__class__.__name__)

        x = Conv2D(64, kernel_size=(3, 3), padding='same', data_format=chan, activation="relu")(input_layer)
        x = MaxPool2D(pool_size=(2, 2), data_format=chan)(x)

        x = Conv2D(filters=128, kernel_size=(3, 3), padding='same', data_format=chan, activation="relu")(x)
        x = MaxPool2D(pool_size=(2, 2), data_format=chan)(x)

        x = Flatten(data_format=chan)(x)
        x = Dense(units=128, activation="relu")(x)

        output_layer = Dense(units=1, activation="sigmoid")(x)
        return input_layer, output_layer

##  4.2 - Model definition and learning

In [15]:
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters

model_generator = AugmentedHandTailoredConvNet()
model_generator.load_dataset_mean_and_variance(mean, variance)

model = model_generator.make_model((3, 224, 224))
# Default Keras learning-rate Value (0.01)
SgdLearningParameters(learning_rate=default_values["learning_rate"]).compile_model(model)
model.summary(expand_nested=True)

In [16]:
import keras

# We fix the number of epochs for now. Later we will add early stopping.
model.fit(x=train_dataloader, validation_data=validation_dataloader, epochs=default_values["epochs"], callbacks=[
    # To persist the history
    keras.callbacks.CSVLogger(f"{project_definition['name']}_train.csv", separator=",", append=False)
])

persist_model: bool = True
if persist_model:
    model.save(f'{project_definition["name"]}.keras')

Convergence is way slower (in fact the model has not stopped improving both on validation and training). <br/>
More epochs could further improve the model so we go on for other 5 epochs.

In [11]:
# model.load_weights(f"{project_definition['name']}.keras")

In [17]:
res = model.evaluate(test_dataloader)
print(f"Test accuracy is {res[1] * 100:.2f}% while loss is {res[0]}")

Convergence was very slow and is not done.

## 4.3 - Results summary

In [45]:
from utils.data_processing import make_loss_graphs, make_loss_accuracy_graphs, add_tuner_iteration_to_data
import pandas

csv = pandas.read_csv(f"{project_definition['name']}_train.csv")
add_tuner_iteration_to_data(csv)

loss_graph = make_loss_graphs(csv)
acc_graph = make_loss_accuracy_graphs(csv)

loss_graph.update_layout(title="Loss vs Val_loss in tuner search per epoch (Val dashed)").show()
acc_graph.update_layout(title="Accuracy vs Val_Accuracy in tuner search per epoch (Val dashed)").show()

The model now seems to be slightly underfitting. The augmentation procedure could be a little too strong.

### 4.3.1 - Comparison with non augmented model
To better make a comparison we should watch K-fold CV means but nothing stops us from making some graphs:

In [49]:
csv

In [54]:
non_augmented_dataframe = pandas.read_csv(f"hand_tailored_v1_train.csv")
augmented_dataframe = pandas.read_csv(f"{project_definition['name']}_train.csv")

non_augmented_dataframe["tuner_iteration"] = "non-augmented"
augmented_dataframe["tuner_iteration"] = "augmented"

csv = pandas.concat([non_augmented_dataframe, augmented_dataframe])
loss_graph = make_loss_graphs(csv)
acc_graph = make_loss_accuracy_graphs(csv)

loss_graph.update_layout(title="Loss vs Val_loss in tuner search per epoch (Val dashed)").show()
acc_graph.update_layout(title="Accuracy vs Val_Accuracy in tuner search per epoch (Val dashed)").show()

# 5 - Second model: less parameters and simpler

## 5.1 - Model definition

In [2]:
project_definition: dict[str, any] = {"name": "hand_tailored_v2"}

In [97]:
from keras.layers import Conv2D, MaxPool2D, Input, Flatten, Dense, Layer
from models.structure.augmentation_wrapper import TorchAugmentationModel


# This class can also be found in the hand_tailored_conv_net.py file
class SmallerHandTailoredConvNet(TorchAugmentationModel):
    def make_layers(self, input_shape: (int, int, int)) -> tuple[Layer, Layer]:
        chan = self.data_format.value
        input_layer = Input(shape=input_shape, name=self.__class__.__name__)

        x = Conv2D(64, kernel_size=(5, 5), padding='same', data_format=chan, activation="relu")(input_layer)
        x = MaxPool2D(pool_size=(2, 2), data_format=chan)(x)

        x = Conv2D(filters=64, kernel_size=(3, 3), padding='same', data_format=chan, activation="relu")(x)
        x = MaxPool2D(pool_size=(2, 2), data_format=chan)(x)

        x = Flatten(data_format=chan)(x)
        x = Dense(units=128, activation="relu")(x)

        output_layer = Dense(units=1, activation="sigmoid")(x)
        return input_layer, output_layer

## 5.2 - Model instance and learning

In [8]:
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters

model_generator = SmallerHandTailoredConvNet()
model_generator.load_dataset_mean_and_variance(mean, variance)

model = model_generator.make_model((3, 224, 224))

# Default Keras learning-rate Value (0.01)
SgdLearningParameters(learning_rate=default_values["learning_rate"]).compile_model(model)

model.summary(expand_nested=True)

It has less parameters so it should have a harder time learning the samples of the training set.<br />
For starters we won't be using the augmentation procedure, then we will apply one but way simpler than the one before.

In [42]:
import keras

# We fix the number of epochs for now. Later we will add early stopping.
model.fit(x=train_dataloader, validation_data=validation_dataloader, epochs=default_values["epochs"], callbacks=[
    # To persist the history
    keras.callbacks.CSVLogger(f"{project_definition['name']}_train.csv", separator=",", append=True)
])

persist_model: bool = True
if persist_model:
    model.save(f'{project_definition["name"]}.keras')

In [43]:
res = model.evaluate(test_dataloader)
print(f"Test accuracy is {res[1] * 100:.2f}% while loss is {res[0]}")

## 5.3 - Results summary

In [44]:
from utils.data_processing import make_loss_graphs, make_loss_accuracy_graphs, add_tuner_iteration_to_data
import pandas

csv = pandas.read_csv(f"{project_definition['name']}_train.csv")
add_tuner_iteration_to_data(csv)

loss_graph = make_loss_graphs(csv)
acc_graph = make_loss_accuracy_graphs(csv)

loss_graph.update_layout(title="Loss vs Val_loss in tuner search per epoch (Val dashed)").show()
acc_graph.update_layout(title="Accuracy vs Val_Accuracy in tuner search per epoch (Val dashed)").show()

# 6 - Regularization
Is the process of managing the training process in order to avoid overfitting (which is the case in our base model).
Image augmentation is considered a regularization technique.

## 6.1 - Early Stopping
Allows to stop training when there is not notable increase in performance on the validation set given.
This of course requires to partition further to keep a validation fold at all times (not only hyperparameters tuning).

We already kept a small part of the data outside of the training set to measure the learning of our models, to apply
early-stopping we simply have to add a callback to the fit method (```EarlyStopping```)

> More can be found here: https://scikit-learn.org/stable/auto_examples/linear_model/plot_sgd_early_stopping.html

In [ ]:
# From now on we use Early stopping to avoid overfitting and better selecting a model.
# We already had a validation split, to better evaluate the learning process, so we better make use of it


## 6.2 - Dropout

Simple yet effective way of reducing overfitting, these are simply layers of the neural network that put some random inputs to 0 during training.
> This technique was found
to improve the performance of neural nets in a wide variety of application domains includ-
ing object classification, digit recognition, speech recognition, document classification and
analysis of computational biology data. This suggests that dropout is a general technique
and is not specific to any domain.
> 
> ~ https://www.cs.toronto.edu/~rsalakhu/papers/srivastava14a.pdf 

In [ ]:
# The noise added by the augmentation and the use of early stopping might be enough as is
# I actually played a little with it and tried it in both the CNNs but the results were underwhelming so I simply discarded it.
# There is already a lot to talk about in this project.

# 7 - Learning parameters fine tuning
While the structure of the network can also be learnt (as in the dedicated notebook) we also try to fine tune
the learning parameters for the best of our "handcrafted" models yet. <br/>
The hyperparameters we are interested in are:
- SGD related:
    - learning_rate
    - momentumt
- epochs -> We use early stopping therefore we can avoid tuning it.
- batch size

In [2]:
project_definition: dict[str, any] = {"name": "hand_tailored_v1_hp_tune"}

## 7.1 - Hyperparameters space definition

In [3]:
from keras_tuner import HyperParameters

hyperparameters = HyperParameters()

# There is no real need to define them here as the Hypermodel defines them directly.
# The real definition is hardwired in the TunableLearningParameters / TunableModelWrapper
hyperparameters.Float(name="lr", min_value=1e-5, max_value=1e-2, sampling='log', step=2)
hyperparameters.Choice(name=f"batch_size", values=[8, 16, 32, 64])
hyperparameters.Float(name="momentum", min_value=0.5, max_value=1, step=0.05)

## 7.2 - Tuning Process

In [4]:
# Define the model wrapper
model_family = SmallerHandTailoredConvNet()
model_family.load_dataset_mean_and_variance(mean, variance)

In [7]:
from utils.my_tuner import HistoryDeletingBayesianOptimization
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParametersTunable
from models.structure.tunable_hypermodel import TunableHyperModel

sgd_learning_parameters = SgdLearningParametersTunable(learning_rate=default_values["learning_rate"])
hypermodel = TunableHyperModel(model_family, sgd_learning_parameters, (3, 224, 224), tune_batch=True)

tuner = HistoryDeletingBayesianOptimization(
    hypermodel,
    hyperparameters=hyperparameters,
    objective='val_loss',
    tune_new_entries=True,
    overwrite=False,
    directory="tuned_models",
    project_name=project_definition["name"],
    max_trials=15
)

In [14]:
import keras
import callbacks.threshold_stop_cb

tuner.search(train_dataloader, epochs=default_values["epochs"], validation_data=validation_dataloader, callbacks=[
    keras.callbacks.CSVLogger(f"{project_definition['name']}_train.csv", separator=",", append=True),
    keras.callbacks.EarlyStopping(monitor='val_loss', patience=5, verbose=1, mode='min'),
    # I want to immediately discard some unusable parameters 
    callbacks.threshold_stop_cb.ThresholdStopCallback(1, 2),
    callbacks.threshold_stop_cb.ThresholdStopCallback(0.6, 4),
])

## 7.3 - Results

In [8]:
tuner.results_summary(5)

# 8 - K-fold CV to evaluate final model

In [26]:
k = 5

In [4]:
best_learning_parameters = {"lr": 0.00512, "momentum": 0.9, "batch_size": 32}

## 8.1 - Dataset loading

In [28]:
from torch.utils.data import DataLoader, ConcatDataset
from dataset.k_fold_dataset_wrapper import KFoldDatasetWrapper

from dataset.dataset_loader import dataset_loader

train, test = dataset_loader((224, 224))
full_dataset = ConcatDataset([train, test])

k_fold_manager = KFoldDatasetWrapper(k)
k_fold_manager.load_data(full_dataset)

## 8.2 - K-fold CV procedure

In [29]:
import dataset
import importlib

importlib.reload(dataset.k_fold_dataset_wrapper)

In [30]:
from models.zero_one_validation_loss import ZeroOneLoss
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters

model_generator = SmallerHandTailoredConvNet()

learning_parameters = SgdLearningParameters(learning_rate=best_learning_parameters["lr"],
                                            metrics=["accuracy", ZeroOneLoss()])
learning_parameters.momentum = best_learning_parameters["momentum"]

In [31]:
results, test_fold_sizes = k_fold_manager.run_k_fold_cv(learning_parameters, model_generator, (3, 224, 224),
                                                        batch_size=best_learning_parameters["batch_size"])

In [47]:
import numpy as np
import pandas as pd

dataframe = pd.DataFrame(results)
dataframe.columns = ["loss", "accuracy", "0-1-loss"]

# To measure 0-1 loss correctly
dataframe["test_size"] = test_fold_sizes
dataframe["0-1-scaled-loss"] = dataframe["0-1-loss"] / dataframe["test_size"]

In [48]:
dataframe

In [51]:
np.average(dataframe[["loss", "accuracy", "0-1-scaled-loss"]], axis=0)

In [ ]:
dataframe.to_csv(f"{project_definition["name"]}_k_fold_cv.csv", index=False)

## 8.3 - K fold to evaluate the first Model


In [2]:
project_definition: dict[str, any] = {"name": "hand_tailored_v1_augmented"}

In [7]:
from torch.utils.data import DataLoader, ConcatDataset
from dataset.k_fold_dataset_wrapper import KFoldDatasetWrapper

from dataset.dataset_loader import dataset_loader

train, test = dataset_loader((224, 224))
full_dataset = ConcatDataset([train, test])

k_fold_manager = KFoldDatasetWrapper(k)
k_fold_manager.load_data(full_dataset)

In [8]:
from models.zero_one_validation_loss import ZeroOneLoss
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters
from models.conv_network.hand_tailored_conv_net import AugmentedHandTailoredConvNet

model_generator = AugmentedHandTailoredConvNet()

learning_parameters = SgdLearningParameters(learning_rate=best_learning_parameters["lr"],
                                            metrics=["accuracy", ZeroOneLoss()])
learning_parameters.momentum = best_learning_parameters["momentum"]

In [9]:
results, test_fold_sizes = k_fold_manager.run_k_fold_cv(learning_parameters, model_generator, (3, 224, 224),
                                                        batch_size=best_learning_parameters["batch_size"])

In [10]:
import numpy as np
import pandas as pd

dataframe = pd.DataFrame(results)
dataframe.columns = ["loss", "accuracy", "0-1-loss"]

# To measure 0-1 loss correctly
dataframe["test_size"] = test_fold_sizes
dataframe["0-1-scaled-loss"] = dataframe["0-1-loss"] / dataframe["test_size"]

In [11]:
dataframe

In [12]:
np.average(dataframe[["loss", "accuracy", "0-1-scaled-loss"]], axis=0)

In [14]:
dataframe.to_csv(f"{project_definition["name"]}_k_fold_cv.csv", index=False)

### 8.3.1 - Final model training

In [3]:
project_definition: dict[str, any] = {"name": "hand_tailored_v1_final"}

In [1]:
from models.zero_one_validation_loss import ZeroOneLoss
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters
from models.conv_network.hand_tailored_conv_net import AugmentedHandTailoredConvNet

model_generator = AugmentedHandTailoredConvNet()

learning_parameters = SgdLearningParameters(learning_rate=best_learning_parameters["lr"],
                                            metrics=["accuracy", ZeroOneLoss()])
learning_parameters.momentum = best_learning_parameters["momentum"]

NameError: name 'best_learning_parameters' is not defined

In [44]:
model_generator.load_dataset_mean_and_variance(mean, variance)
model = model_generator.make_model((3, 224, 224))
learning_parameters.compile_model(model)

In [45]:
import keras

# We fix the number of epochs for now. Later we will add early stopping.
model.fit(x=train_dataloader, validation_data=validation_dataloader, epochs=80, callbacks=[
    # To persist the history
    keras.callbacks.CSVLogger(f"{project_definition['name']}_train.csv", separator=",", append=True),
    keras.callbacks.EarlyStopping(monitor='val_loss', min_delta=1e-2, patience=5, verbose=1, mode='min'),
])

persist_model: bool = True
if persist_model:
    model.save(f'{project_definition["name"]}.keras')

Epoch 1/80
  1/130 ━━━━━━━━━━━━━━━━━━━━ 1:14 576ms/step - accuracy: 0.4062 - loss: 0.7265 - total_0-1_loss: 19.0000

/home/jacopo/miniconda3/envs/keras-pytorch/lib/python3.12/site-packages/keras/src/backend/torch/nn.py:412: UserWarning:

Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at /opt/conda/conda-bld/pytorch_1704987296916/work/aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)



130/130 ━━━━━━━━━━━━━━━━━━━━ 54s 412ms/step - accuracy: 0.6257 - loss: 0.6643 - total_0-1_loss: 720.9619 - val_accuracy: 0.7597 - val_loss: 0.5161 - val_total_0-1_loss: 142.0000
Epoch 2/80
130/130 ━━━━━━━━━━━━━━━━━━━━ 54s 417ms/step - accuracy: 0.7647 - loss: 0.4978 - total_0-1_loss: 490.8702 - val_accuracy: 0.8308 - val_loss: 0.4154 - val_total_0-1_loss: 100.0000
Epoch 3/80
130/130 ━━━━━━━━━━━━━━━━━━━━ 53s 406ms/step - accuracy: 0.8034 - loss: 0.4560 - total_0-1_loss: 413.9084 - val_accuracy: 0.8409 - val_loss: 0.3854 - val_total_0-1_loss: 94.0000
Epoch 4/80
130/130 ━━━━━━━━━━━━━━━━━━━━ 53s 406ms/step - accuracy: 0.8157 - loss: 0.4068 - total_0-1_loss: 385.8015 - val_accuracy: 0.8156 - val_loss: 0.4284 - val_total_0-1_loss: 109.0000
Epoch 5/80
130/130 ━━━━━━━━━━━━━━━━━━━━ 54s 417ms/step - accuracy: 0.8332 - loss: 0.3927 - total_0-1_loss: 355.2443 - val_accuracy: 0.8426 - val_loss: 0.3897 - val_total_0-1_loss: 93.0000
Epoch 6/80
130/130 ━━━━━━━━━━━━━━━━━━━━ 52s 405ms/step - accuracy: 0

### 8.3.2 - Model evaluation

In [9]:
model_generator.load_dataset_mean_and_variance(mean, variance)
model = model_generator.make_model((3, 224, 224))

model.load_weights(f"{project_definition['name']}.keras")

In [11]:
import keras

# We add the wanted metrics
learning_parameters = SgdLearningParameters(learning_rate=best_learning_parameters["lr"],
                                            momentum=best_learning_parameters["momentum"], metrics=[
        "accuracy", ZeroOneLoss(),

        # To evaluate the model now.
        keras.metrics.TruePositives(name="tp"),
        keras.metrics.FalsePositives(name="fp"),

        keras.metrics.TrueNegatives(name="tn"),
        keras.metrics.FalseNegatives(name="fn")
    ])

learning_parameters.compile_model(model)

In [13]:
evaluation = model.evaluate(test_dataloader, return_dict=True)
print(f"Test accuracy is {evaluation['accuracy'] * 100:.2f}% while loss is {evaluation['loss']}")

37/37 ━━━━━━━━━━━━━━━━━━━━ 12s 335ms/step - accuracy: 0.8963 - fn: 42.7368 - fp: 20.0263 - loss: 0.2691 - tn: 315.3684 - total_0-1_loss: 62.7632 - tp: 245.0263
Test accuracy is 89.95% while loss is 0.262251079082489


In [15]:
# Confusion Matrix
import plotly.express as px

confusion_matrix = px.imshow([[evaluation["tp"], evaluation["fp"]], [evaluation["fn"], evaluation["tn"]]],
                             labels=dict(x="Predicted label", y="True label", color="Productivity"),
                             text_auto=True, x=["1", "0"], y=["1", "0"], template="plotly")
confusion_matrix.update(layout_coloraxis_showscale=False)
confusion_matrix.update_layout(xaxis_nticks=4, yaxis_nticks=4, width=400, height=400)
confusion_matrix.show()

In [17]:
# Precision - Recall - F1
m_precision = evaluation["tp"] / (evaluation["tp"] + evaluation["fp"])
m_recall = evaluation["tp"] / (evaluation["tp"] + evaluation["fn"])
c_precision = evaluation["tn"] / (evaluation["tn"] + evaluation["fn"])
c_recall = evaluation["tn"] / (evaluation["tn"] + evaluation["fp"])

print(
    f"Muffin: precision={m_precision}, recall={m_recall}, F1={2 * ((m_precision * m_recall) / (m_precision + m_recall))}\n"
    f"Chihuahua: precision={c_precision}, recall={c_recall}, F1={2 * ((c_precision * c_recall) / (c_precision + c_recall))}"
)

Muffin: precision=0.8419117647058824, recall=0.9308943089430894, F1=0.8841698841698841
Chihuahua: precision=0.946875, recall=0.8757225433526011, F1=0.9099099099099098


## 8.4 - K-Fold to evaluate the second model

In [95]:
project_definition: dict[str, any] = {"name": "hand_tailored_v2"}

In [98]:
from models.zero_one_validation_loss import ZeroOneLoss
from models.structure.learning_parameters.sgd_learning_parameters import SgdLearningParameters
from models.conv_network.hand_tailored_conv_net import AugmentedHandTailoredConvNet

model_generator = SmallerHandTailoredConvNet()

learning_parameters = SgdLearningParameters(learning_rate=best_learning_parameters["lr"],
                                            metrics=["accuracy", ZeroOneLoss()])
learning_parameters.momentum = best_learning_parameters["momentum"]

In [30]:
results, test_fold_sizes = k_fold_manager.run_k_fold_cv(learning_parameters, model_generator, (3, 224, 224),
                                                        batch_size=best_learning_parameters["batch_size"])

In [31]:
import numpy as np
import pandas as pd

dataframe = pd.DataFrame(results)
dataframe.columns = ["loss", "accuracy", "0-1-loss"]

# To measure 0-1 loss correctly
dataframe["test_size"] = test_fold_sizes
dataframe["0-1-scaled-loss"] = dataframe["0-1-loss"] / dataframe["test_size"]

In [34]:
dataframe

In [32]:
np.average(dataframe[["loss", "accuracy", "0-1-scaled-loss"]], axis=0)

In [33]:
dataframe.to_csv(f"{project_definition["name"]}_k_fold_cv.csv", index=False)

### 8.4.1 - Final model training

In [37]:
project_definition: dict[str, any] = {"name": "hand_tailored_v2_final"}

In [99]:
model_generator.load_dataset_mean_and_variance(mean, variance)
model = model_generator.make_model((3, 224, 224))
learning_parameters.compile_model(model)

In [41]:
import keras

# We fix the number of epochs for now. Later we will add early stopping.
model.fit(x=train_dataloader, validation_data=validation_dataloader, epochs=80, callbacks=[
    # To persist the history
    keras.callbacks.CSVLogger(f"{project_definition['name']}_train.csv", separator=",", append=True),
    keras.callbacks.EarlyStopping(monitor='val_loss', min_delta=1e-2, patience=5, verbose=1, mode='min'),
])

persist_model: bool = True
if persist_model:
    model.save(f'{project_definition["name"]}.keras')

In [42]:
res = model.evaluate(test_dataloader)
print(f"Test accuracy is {res[1] * 100:.2f}% while loss is {res[0]}")

In [44]:
res[2] / len(test)

### 8.4.2 - Model evaluation

In [108]:
model_generator = SmallerHandTailoredConvNet()
model_generator.load_dataset_mean_and_variance(mean, variance)

model = model_generator.make_model((3, 224, 224))
model.load_weights(f"{project_definition['name']}.keras")

In [109]:
# We add the wanted metrics
learning_parameters = SgdLearningParameters(learning_rate=best_learning_parameters["lr"],
                                            momentum=best_learning_parameters["momentum"], metrics=[
        "accuracy", ZeroOneLoss(),

        # To evaluate the model now.
        keras.metrics.TruePositives(name="tp"),
        keras.metrics.FalsePositives(name="fp"),

        keras.metrics.TrueNegatives(name="tn"),
        keras.metrics.FalseNegatives(name="fn")
    ])

learning_parameters.compile_model(model)

In [112]:
evaluation = model.evaluate(test_dataloader, return_dict=True)

print(evaluation)  # print whole object
print(
    f"Test accuracy is {evaluation['accuracy'] * 100:.2f}% while loss is {evaluation['loss']} and 0-1 loss is {evaluation['total_0-1_loss'] / len(test_dataloader.dataset)}")

37/37 ━━━━━━━━━━━━━━━━━━━━ 13s 334ms/step - accuracy: 0.8968 - fn: 36.9211 - fp: 29.0000 - loss: 0.2474 - tn: 308.0000 - total_0-1_loss: 65.9211 - tp: 249.2368
{'accuracy': 0.8969594836235046, 'fn': 66.0, 'fp': 56.0, 'loss': 0.24806079268455505, 'tn': 584.0, 'total_0-1_loss': 122.0, 'tp': 478.0}
Test accuracy is 89.70% while loss is 0.24806079268455505 and 0-1 loss is 0.10304054054054054


In [113]:
# Confusion Matrix
import plotly.express as px

confusion_matrix = px.imshow([[evaluation["tp"], evaluation["fp"]], [evaluation["fn"], evaluation["tn"]]],
                             labels=dict(x="Predicted label", y="True label", color="Productivity"),
                             text_auto=True, x=["1", "0"], y=["1", "0"], template="plotly")
confusion_matrix.update(layout_coloraxis_showscale=False)
confusion_matrix.update_layout(xaxis_nticks=4, yaxis_nticks=4, width=400, height=400)
confusion_matrix.show()

In [130]:
# Precision - Recall - F1
m_precision = evaluation["tp"] / (evaluation["tp"] + evaluation["fp"])
m_recall = evaluation["tp"] / (evaluation["tp"] + evaluation["fn"])
c_precision = evaluation["tn"] / (evaluation["tn"] + evaluation["fn"])
c_recall = evaluation["tn"] / (evaluation["tn"] + evaluation["fp"])

print(
    f"Muffin: precision={m_precision}, recall={m_recall}, F1={2 * ((m_precision * m_recall) / (m_precision + m_recall))}\n"
    f"Chihuahua: precision={c_precision}, recall={c_recall}, F1={2 * ((c_precision * c_recall) / (c_precision + c_recall))}"
)

Muffin: precision=0.8951310861423221, recall=0.8786764705882353, F1=0.8868274582560297
Chihuahua: precision=0.8984615384615384, recall=0.9125, F1=0.9054263565891473
